In [17]:
import pandas as pd
import numpy as np
import csv
import copy
import altair as alt
from collections import Counter
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
nltk.download('punkt')
import string
from statsmodels.distributions.empirical_distribution import ECDF
import re
from unidecode import unidecode
from collections import defaultdict

alt.data_transformers.enable('default', max_rows=None)  #renders if the df has more than 5000 rows

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\giang\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\giang\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


DataTransformerRegistry.enable('default')

In [2]:
path = "E:\Gianluca\Master Big Data Pisa\Progetto_Finale\Agricolo\Facebook\csv_docs_def\comments4_no_spam_nan.csv"
comments_no_nan = pd.read_csv(path, parse_dates=["post_date"], quotechar='"', quoting=csv.QUOTE_ALL, encoding="utf-8", low_memory=False)

In [3]:
def replace_dots(text):
    # This pattern will match sequences of words separated by dots but not acronyms.
    # Acronyms are sequences of single uppercase letters separated by dots and potentially followed by a dot.
    #pattern = r'\b(?:\w+\.\w{2,}|\w{2,}\.\w+)(?:\.\w+)*\b'
    pattern = r'\b(?:[a-zA-Z]+\.[a-zA-Z]{2,}|[a-zA-Z]{2,}\.[a-zA-Z]+)(?:\.[a-zA-Z]+)*\b'
    #pattern = r'\b(?!\d{1,2}\.\d{1,2}\.\d{2,4}\b)(?=\w*[^\d]\w*)(?:\w{2,}\.\w+|\w+\.\w{2,})(?:\.\w+)*\b'

    def replacement(match):
        # Replace dots with spaces in the matched string
        return match.group(0).replace('.', '. ')
    
    # Use re.sub to replace the matched pattern with the replacement function
    return re.sub(pattern, replacement, text)

# Example usage
text = "I.am.italian and this.is.a.test but u.s.a. should not.match 17.04.1991 or 3.5.2020."
result = replace_dots(text)
print(result)

I. am. italian and this. is. a. test but u.s.a. should not. match 17.04.1991 or 3.5.2020.


In [4]:
def replace_commas(text):
    # This pattern will match sequences of words separated by dots but not acronyms.
    # Acronyms are sequences of single uppercase letters separated by dots and potentially followed by a dot.
    #pattern = r'\b(?:\w+\.\w{2,}|\w{2,}\.\w+)(?:\.\w+)*\b'
    pattern = r'\b(?:[a-zA-Z]+,[a-zA-Z]{2,}|[a-zA-Z]{2,},[a-zA-Z]+)(?:,[a-zA-Z]+)*\b'
    #pattern = r'\b(?!\d{1,2}\.\d{1,2}\.\d{2,4}\b)(?=\w*[^\d]\w*)(?:\w{2,}\.\w+|\w+\.\w{2,})(?:\.\w+)*\b'

    def replacement(match):
        # Replace dots with spaces in the matched string
        return match.group(0).replace(',', ', ')
    
    # Use re.sub to replace the matched pattern with the replacement function
    return re.sub(pattern, replacement, text)

# Example usage
text = "I,am,italian and this,is,a,test but u,s,a. should not,match 17,04,1991 or 3,5,2020,"
result = replace_commas(text)
print(result)

I, am, italian and this, is, a, test but u,s,a. should not, match 17,04,1991 or 3,5,2020,


In [5]:
def clean_text(text):
    # Rimuove gli articoli con apostrofi come "l'", "all'", ecc.
    cleaned_text = re.sub(r"^(l|all|d|nell|sull|coll|dall|dell|all|quell|quest)'", '', text)
    return cleaned_text

In [6]:
def remove_leading_point(text):
    # Define a pattern to match words starting with a point
    #pattern = r'\W\.\b(?=\w+)'
    pattern = r'(?:(?<=\s)|(?<=^))\.\b(?=\w+)'

    # Use re.sub to remove the leading point from matched words
    result = re.sub(pattern, '', text)

    return result

# Example usage
#text = ".example with .words. starting .with points, no match u.s.a."
text = ".casa"
result = remove_leading_point(text)
print(result)

casa


In [7]:
def remove_ending_point(text):
    # Define a pattern to match words starting with a point
    #pattern = r'\W\.\b(?=\w+)'
    pattern = r'(?:\b)\.$'

    # Use re.sub to remove the leading point from matched words
    result = re.sub(pattern, '', text)

    return result

# Example usage
#text = ".example with .words. starting .with points, no match u.s.a."
text = "example. with. .words. starting .with points, no match u.s.a."
result = remove_ending_point(text)
print(result)

example. with. .words. starting .with points, no match u.s.a


In [8]:
def remove_hyphen(text):
    # Define a pattern to match words starting with a point
    #pattern = r'\W\.\b(?=\w+)'
    pattern = r'(?<=[a-zA-Z])-(?=[a-zA-Z])'

    # Use re.sub to remove the leading point from matched words
    result = re.sub(pattern, ' ', text)

    return result

# Example usage
#text = ".example with .words. starting .with points, no match u.s.a."
text = "example-with-words. starting with points, no-match u.s.a., no match 21-02 21-02-98"
result = remove_hyphen(text)
print(result)

example with words. starting with points, no match u.s.a., no match 21-02 21-02-98


In [9]:
def remove_link(text):   
    
    pattern = r'\bhttps?\S+|\bcom/share\S+|\bstory_fbid=\S+|\bcom/story\S+'
    result = re.sub(pattern, '', text)

    return result

text = "Here are some URLs: https://example.com, https://test-site.org, and an other one http://wrong.com and com/share/jfdoijg and story_fbid=57489."
result = remove_link(text)
print(result)

Here are some URLs:   and an other one  and  and 


In [10]:
from nltk.corpus import stopwords
STOPWORDS = set(stopwords.words('italian')) # ovviamente le stopwords sono diverse da lingua a lingua, inoltre in stopwords.words('italian') sono 
                                                # tutte minuscole
SCARTO = [] # si può procedere a mano
def filter_words(words):
    return [w for w in words if w not in STOPWORDS and w not in SCARTO] # filtro

# c = Counter(filter_words(tokens))

In [10]:
def transform_text(text):
    text = str(text).lower()
    text = unidecode(text)
    text = replace_dots(text)
    text = replace_commas(text)
    text = remove_leading_point(text)
    text = remove_hyphen(text)
    text = remove_link(text)
    return text

In [28]:
count = 0
for index, row in comments_no_nan.iterrows():
    print(row["content"])
    text = transform_text(row['content'])
    print(text)
    print("-------------------------------------------------------")
    count = count + 1
    if count >= 20:
        break

Il clima viene controllato con la tecnologia
il clima viene controllato con la tecnologia
-------------------------------------------------------
Yes  tutto una manipolazione del clima adesso anno tecnologico su tutto ma noi popolo ni sappiamo poco
yes  tutto una manipolazione del clima adesso anno tecnologico su tutto ma noi popolo ni sappiamo poco
-------------------------------------------------------
Fresco? C'è il rischio che non rimanga nessun frutto tra grandine, neve e gelo,speriamo bene.
fresco? c'e il rischio che non rimanga nessun frutto tra grandine, neve e gelo, speriamo bene.
-------------------------------------------------------
Maccioni Bruno colpa del riscaldamento globale
maccioni bruno colpa del riscaldamento globale
-------------------------------------------------------
Giuseppe Quattromini Questo io non sono in grado di stabilirlo, posso dire che mio suocero mi raccontava che il mese di giugno negli anni 40/ta in Molise gelò il grano.
giuseppe quattromini questo 

In [29]:
transform_text("I.am.italiàn and this.is.a.test but u.s.a. should not.match 17.04.1991 or 3.5.2020.")
transform_text("l'attraversamento del ba.arè.af")

"l'attraversamento del ba. are. af"

In [80]:
from nltk.corpus import stopwords
STOPWORDS = set(stopwords.words('italian'))
STOPWORDS.update(string.punctuation)
unwanted_words = ["..", "....", "...", "piu", "solo", "perche", "grazie", "fare", "cosi", "cosa", "senza", "essere", "mai", "poi", ".....", "no", '"', "tutte", "x", "fa", "quando", '``', "''", "fate"]
STOPWORDS.update(unwanted_words)

all_tokens = []
for index, row in comments_no_nan.iterrows():
    text = transform_text(row["content"])
    tokenized_comment = nltk.word_tokenize(text, language='italian')
    for word in tokenized_comment:
        if word not in STOPWORDS and word != "":
            temp = clean_text(word)
            temp = remove_leading_point(temp)
            temp = remove_ending_point(temp)
            all_tokens.append(temp)

In [81]:
freq_dist = nltk.FreqDist(all_tokens)
freq_dist

FreqDist({'agricoltori': 11639, 'forza': 10697, 'sempre': 8545, 'italia': 7125, 'italiani': 6093, 'avanti': 6035, 'dio': 4742, 'bravi': 4620, 'tutta': 4400, 'prodotti': 4201, ...})

In [82]:
freq_dist = dict(freq_dist)

In [83]:
len(freq_dist)

72475

In [84]:
sum(freq_dist.values())

1056559

In [85]:
sorted(freq_dist.items(), key=lambda x: x[1])

[('40/ta', 1),
 ('ricaldamento', 1),
 ('slacciassero', 1),
 ('stratagemma', 1),
 ('1985', 1),
 ('catria', 1),
 ('scioglievano', 1),
 ('gelare', 1),
 ('matematico', 1),
 ('aderente', 1),
 ('eminenti', 1),
 ('questo', 1),
 ('approssimativamente', 1),
 ('vagliate', 1),
 ('terrapiattismo', 1),
 ('conobbe', 1),
 ('allarmista', 1),
 ('febbre', 1),
 ('previsionale', 1),
 ('sovrastimi', 1),
 ('fisiologiche', 1),
 ('incamminarci', 1),
 ('catastrofistica', 1),
 ('oggettive', 1),
 ('appiattirsi', 1),
 ('eretiche', 1),
 ('suicidarci', 1),
 ('modestissimo', 1),
 ('proporzionali', 1),
 ('demografico', 1),
 ('numerico', 1),
 ('decimato', 1),
 ("'nella", 1),
 ('estinzioni', 1),
 ('anzitempo', 1),
 ('giustificazioni', 1),
 ('esponenziali', 1),
 ('fermarne', 1),
 ('protezioen', 1),
 ('linseminazione', 1),
 ('estensivamente', 1),
 ('deforesta', 1),
 ('cataloga', 1),
 ('positano', 1),
 ('22deg', 1),
 ('23:30', 1),
 ('fioccava', 1),
 ('aeree', 1),
 ('innaffiando', 1),
 ('metodologia', 1),
 ('paurosa', 1),


In [86]:
sorted(freq_dist.items(), key=lambda x: -x[1])

[('agricoltori', 11639),
 ('forza', 10697),
 ('sempre', 8545),
 ('italia', 7125),
 ('italiani', 6093),
 ('avanti', 6035),
 ('dio', 4742),
 ('bravi', 4620),
 ('tutta', 4400),
 ('prodotti', 4201),
 ('mollate', 3872),
 ('popolo', 3768),
 ('lavoro', 3727),
 ('ragazzi', 3535),
 ('roma', 3488),
 ('bene', 3289),
 ('terra', 3144),
 ('italiano', 3136),
 ('ora', 2997),
 ('grandi', 2990),
 ('benedica', 2837),
 ('agricoltura', 2801),
 ('grande', 2784),
 ('europa', 2748),
 ('bravissimi', 2727),
 ('governo', 2719),
 ('complimenti', 2573),
 ('fatto', 2513),
 ('bisogna', 2440),
 ('dobbiamo', 2360),
 ('anni', 2352),
 ('altri', 2265),
 ('parte', 2226),
 ('politici', 2224),
 ('buona', 2174),
 ('vogliono', 2154),
 ('deve', 2144),
 ('niente', 2143),
 ('gia', 2115),
 ('nulla', 2060),
 ('uniti', 2052),
 ('vita', 2024),
 ('nessuno', 2017),
 ('ancora', 1999),
 ('basta', 1932),
 ('gente', 1871),
 ('mondo', 1859),
 ('nn', 1850),
 ('andare', 1847),
 ('buon', 1841),
 ('puo', 1836),
 ('vero', 1824),
 ('molto', 1810

In [87]:
freq_df = pd.DataFrame(list(freq_dist.items()), columns=['Token', 'Frequency'])
freq_df = freq_df.sort_values(by="Frequency", ascending=False)

In [88]:
# Create a line plot
line_chart = alt.Chart(freq_df[:50]).mark_line().encode(
    y=alt.Y('Frequency', type="quantitative", title='frequency'),
    x=alt.X('Token', type="nominal", title='tokens', sort="-y")
).properties(
    title='token frequency'
)

line_chart.properties(width=800, height=600)

alt.Chart(...)

# Lemmatizzazione

pip install spacy

In [91]:
import spacy.cli
spacy.cli.download('en_core_web_sm')
spacy.cli.download('it_core_news_sm')

⚠ As of spaCy v3.0, shortcuts like 'en' are deprecated. Please use the
full pipeline package name 'en_core_web_sm' instead.
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.
⚠ As of spaCy v3.0, shortcuts like 'it' are deprecated. Please use the
full pipeline package name 'it_core_news_sm' instead.
✔ Download and installation successful
You can now load the package via spacy.load('it_core_news_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [92]:
import spacy
nlp = spacy.load('en_core_web_sm')
nlp = spacy.load('it_core_news_sm')

In [118]:
from nltk.corpus import stopwords
STOPWORDS = set(stopwords.words('italian'))
STOPWORDS.update(string.punctuation)
unwanted_words = ["..", "....", "...", "piu", "solo", "perche", "grazie", "fare", "cosi", "cosa", "senza", "essere", "mai", "poi", ".....", "no", '"', "tutte", "x", "fa", "quando", '``', "''", "fate"]
STOPWORDS.update(unwanted_words)

all_lemmas = []
for index, row in comments_no_nan.iterrows():
    text = transform_text(row["content"])
    tokenized_comment = nltk.word_tokenize(text, language='italian')
    for word in tokenized_comment:
        if word not in STOPWORDS and word != "":
            temp = clean_text(word)
            temp = remove_leading_point(temp)
            temp = remove_ending_point(temp)
            temp = nlp(temp)
            all_lemmas.append(temp[0].lemma_)

In [117]:
tokenized_comment = nlp("richiedo")
print(tokenized_comment[0].lemma_)
for word in tokenized_comment:
    print(word.lemma_)

richiedere
richiedere


In [120]:
freq_dist_lemmas = nltk.FreqDist(all_lemmas)
freq_dist_lemmas

FreqDist({'agricoltore': 12505, 'dovere': 11386, 'forza': 11077, 'italiano': 11007, 'bravo': 10991, 'sempre': 8546, 'volere': 7681, 'andare': 7310, 'Italia': 7125, 'grande': 6115, ...})

In [121]:
freq_dist_lemmas = dict(freq_dist_lemmas)

In [122]:
len(freq_dist_lemmas)

57290

In [123]:
sum(freq_dist_lemmas.values())

1056559

In [124]:
sorted(freq_dist_lemmas.items(), key=lambda x: x[1])

[('ricaldamento', 1),
 ('slacciasserare', 1),
 ('stratagemma', 1),
 ('1985', 1),
 ('catrio', 1),
 ('gelare', 1),
 ('matematico', 1),
 ('eminento', 1),
 ('approssimativamente', 1),
 ('terrapiattismo', 1),
 ('allarmista', 1),
 ('febbre', 1),
 ('previsionale', 1),
 ('sovrastimo', 1),
 ('fisiologica', 1),
 ('incamminare ci', 1),
 ('catastrofistico', 1),
 ('appiattire si', 1),
 ('eretica', 1),
 ('suicidare ci', 1),
 ('modeste', 1),
 ('proporzionale', 1),
 ('demografico', 1),
 ('anzitempo', 1),
 ('fermare ne', 1),
 ('protezioenre', 1),
 ('linseminazione', 1),
 ('estensivamente', 1),
 ('deforesta', 1),
 ('cataloga', 1),
 ('positare', 1),
 ('22deg', 1),
 ('23:30', 1),
 ('metodologiare', 1),
 ('soprabire', 1),
 ('desertifichere', 1),
 ('chiuderai', 1),
 ('subiro', 1),
 ('coesistere', 1),
 ('disboscamento', 1),
 ('vate te lo', 1),
 ('zicchicco', 1),
 ('1990/2000', 1),
 ('2000/2010', 1),
 ('25/26', 1),
 ('tramontana', 1),
 ('classificarre lo', 1),
 ('chiudito', 1),
 ('minckjiare', 1),
 ('robertoa

In [125]:
sorted(freq_dist_lemmas.items(), key=lambda x: -x[1])

[('agricoltore', 12505),
 ('dovere', 11386),
 ('forza', 11077),
 ('italiano', 11007),
 ('bravo', 10991),
 ('sempre', 8546),
 ('volere', 7681),
 ('andare', 7310),
 ('Italia', 7125),
 ('grande', 6115),
 ('avanti', 6035),
 ('mollare', 5265),
 ('dire', 5230),
 ('potere', 5007),
 ('vedere', 4957),
 ('buono', 4925),
 ('altro', 4792),
 ('fare', 4751),
 ('Dio', 4742),
 ('essere', 4557),
 ('tutto', 4527),
 ('bene', 4263),
 ('prodotto', 4201),
 ('tanto', 4196),
 ('politico', 4175),
 ('bello', 4087),
 ('lavoro', 3979),
 ('sapere', 3799),
 ('ragazzo', 3789),
 ('Popolo', 3768),
 ('anno', 3682),
 ('Roma', 3488),
 ('terra', 3473),
 ('governo', 3256),
 ('ora', 3217),
 ('vero', 3189),
 ('nessuno', 3070),
 ('mangiare', 2997),
 ('benedica', 2837),
 ('molto', 2814),
 ('agricoltura', 2813),
 ('Europa', 2751),
 ('bisognare', 2700),
 ('venire', 2596),
 ('complimento', 2573),
 ('paese', 2410),
 ('dare', 2379),
 ('parte', 2366),
 ('capire', 2288),
 ('parlare', 2251),
 ('protestare', 2242),
 ('sperare', 2191),


In [126]:
freq_df = pd.DataFrame(list(freq_dist_lemmas.items()), columns=['Token', 'Frequency'])
freq_df = freq_df.sort_values(by="Frequency", ascending=False)

In [127]:
# Create a line plot
line_chart = alt.Chart(freq_df[:50]).mark_line().encode(
    y=alt.Y('Frequency', type="quantitative", title='frequency'),
    x=alt.X('Token', type="nominal", title='tokens', sort="-y")
).properties(
    title='token frequency'
)

line_chart.properties(width=800, height=600)

alt.Chart(...)

# Collocations

In [19]:
def remove_receiver(row):
    if row["level"] > 0 and isinstance(row["content"], str):
        receiver_name_len = len(row["type"].split()) - len(row["author"].split()) - 7
        if len(row["content"].split()) >= receiver_name_len:
            token_list = row["content"].split()
            del token_list[:receiver_name_len]
            content_without_receiver = " ".join(token_list)
            row["content"] = content_without_receiver
    return row

# Apply the function to each row
comments_truncated = comments_no_nan.apply(remove_receiver, axis=1)

In [13]:
sents = list()
for text in comments_truncated["content"]:
    sents.append(nltk.word_tokenize(transform_text(text), language='italian'))

In [18]:
from gensim.models.phrases import Phraser, Phrases

In [19]:
bigram = Phraser(Phrases(sents, min_count=2, threshold=1))

In [28]:
collocations = list()
for key in bigram.phrasegrams:
    score = bigram.phrasegrams[key]
    collocations.append((''.join([word for word in key]), score))

for (coll,score) in sorted(collocations,key=lambda x: x[1], reverse=True):
    print(f'"{coll}", score={score}')

"cri_minali", score=245022.40000000002
"falda_acquifera", score=76569.5
".he_informs", score=76569.5
"translated_into", score=76569.5
"explaining_arbitration", score=76569.5
"active_citizens", score=76569.5
"rights_organizations", score=76569.5
"medical_doctors", score=76569.5
"deretor_geniral", score=76569.5
"14-02-2024_h17:05", score=76569.5
"sull'articolo_1277", score=76569.5
"l'altopianonoi_penetriamo", score=76569.5
"quelledel_centrosinistra", score=76569.5
"saamhorigheid_geweldig", score=76569.5
"l'ampia_ricaduta", score=76569.5
"parteciparevenetomatteo_perra3805980866lombardiapaolo", score=76569.5
"perra3805980866lombardiapaolo_giarretta3312239085friuli", score=76569.5
"giuliaclaudio_sist3493091400piemontepaola", score=76569.5
"sist3493091400piemontepaola_ponzo3391276654emilia", score=76569.5
"ponzo3391276654emilia_romagnaluisito", score=76569.5
"romagnaluisito_naldi3358155205toscanafabio", score=76569.5
"naldi3358155205toscanafabio_mecarozzi3772833252laziogiancarlo", score=7656

In [33]:
# Applying the bigram detector to sentences
bigram_sentences = [bigram[sentence] for sentence in sents]

# Flatten the list of lists
flat_list = [item for sublist in bigram_sentences for item in sublist]

# Counting the frequency of collocations
collocation_counter = Counter(flat_list)

# Filter out single words, keeping only bigrams
#collocations_freq = {k: (v, bigram.phrasegrams[k]) for k, v in collocation_counter.items() if '_' in k}
collocations_freq = {}
for k, v in collocation_counter.items():
    if '_' in k:
        try:
            collocations_freq[k] = (v, bigram.phrasegrams[k])
        except:
            collocations_freq[k] = (v, 0)

print(collocations_freq)

{'il_clima': (51, 11.17045621581476), 'con_la': (1283, 1.1537383985442502), 'una_manipolazione': (3, 3.5404586859018816), 'del_clima': (16, 12.363291415762781), 'su_tutto': (151, 6.6988515191767855), 'noi_popolo': (80, 2.014175490828845), "c_'": (1561, 50.12648679105498), 'il_rischio': (18, 7.079457965347537), 'non_rimanga': (7, 3.9075541266378333), 'grandine_,': (5, 2.3618551881358956), 'neve_e': (7, 1.3418784267581303), 'speriamo_bene': (84, 17.022508324084352), 'colpa_del': (8, 6.1587711735533865), 'riscaldamento_globale': (9, 4794.958904109589), 'io_non': (534, 1.2587143521725301), 'in_grado': (79, 21.061027984506243), 'posso_dire': (32, 28.916152363672936), 'mio_suocero': (7, 217.89840637450197), 'mi_raccontava': (8, 69.00484397882168), 'mese_di': (12, 1.1794075968084778), 'negli_anni': (82, 55.22253775073247), 'il_grano': (230, 7.189846043906755), '!_!': (21636, 5.02499740961466), 'i_politici': (549, 8.14203738767037), 'sempre_al': (119, 1.2915616197676238), 'la_cravatta': (4, 2.

In [34]:
collocations_freq_list = sorted(collocations_freq.items(), key=lambda x:-x[1][0])
collocations_freq_list

[('!_!', (21636, 5.02499740961466)),
 ('con_voi', (3731, 15.839487237436716)),
 ('non_mollate', (3548, 13.062915036903092)),
 ('?_?', (3464, 9.406197565893338)),
 ('siamo_con', (3299, 11.427575593739617)),
 ('non_si', (2863, 2.486326645778549)),
 (',_ma', (2696, 1.8303463677407628)),
 ('gli_agricoltori', (2562, 23.99925536225849)),
 ('che_dio', (2176, 6.225283193534317)),
 ('avanti_tutta', (1959, 50.47252096652855)),
 ('forza_ragazzi', (1875, 30.68232990632317)),
 ('tutti_i', (1848, 2.9562433516423035)),
 ('quello_che', (1777, 10.297163299521102)),
 ('a_roma', (1777, 12.075814135062961)),
 ('in_italia', (1667, 12.465702173689442)),
 ('i_nostri', (1645, 15.981121574141682)),
 ('il_popolo', (1574, 10.760443738409695)),
 ('la_nostra', (1563, 12.817370401989853)),
 ("c_'", (1561, 50.12648679105498)),
 ('se_non', (1501, 2.145307299307612)),
 ('a_tutti', (1470, 2.400966881520907)),
 ('che_ci', (1457, 2.1366198472090767)),
 ('vi_benedica', (1421, 53.05603902673603)),
 ("l_'", (1314, 27.526979

In [51]:
#from nltk.corpus import stopwords
#stopwords = stopwords.words('italian')

In [53]:
from nltk.corpus import stopwords

stopwords = set(stopwords.words('italian'))
stopwords.update(string.punctuation)
stopwords = list(stopwords)

In [37]:
from gensim.models.phrases import ENGLISH_CONNECTOR_WORDS

ENGLISH_CONNECTOR_WORDS

frozenset({'a',
           'an',
           'and',
           'at',
           'by',
           'for',
           'from',
           'in',
           'of',
           'on',
           'or',
           'the',
           'to',
           'with',
           'without'})

In [22]:
ITALIAN_CONNECTOR_WORDS = frozenset({"un", "un'", "uno", "una", "e", "ed", "a", "da", "per", "in", "nel", "negli", "nelle", "di", "d'", "su", "sul", "sulla", "sullo", "sugli", "sulle", "o", "il", "lo", "la", "le", "i", "l'", "gli", "degli", "delle", "dell'","con", "senza", "che"})

In [48]:
ITALIAN_CONNECTOR_WORDS

frozenset({'a',
           'con',
           "d'",
           'da',
           'degli',
           "dell'",
           'delle',
           'di',
           'e',
           'ed',
           'gli',
           'i',
           'il',
           'in',
           "l'",
           'la',
           'le',
           'lo',
           'o',
           'per',
           'senza',
           'su',
           'un',
           "un'",
           'una',
           'uno'})

In [31]:
bigram = Phraser(Phrases(sents, connector_words=stopwords))

In [36]:
collocations = list()
for key in bigram.phrasegrams:
    score = bigram.phrasegrams[key]
    collocations.append((''.join([word for word in key]), score))

In [37]:
# Applying the bigram detector to sentences
bigram_sentences = [bigram[sentence] for sentence in sents]

# Flatten the list of lists
flat_list = [item for sublist in bigram_sentences for item in sublist]

# Counting the frequency of collocations
collocation_counter = Counter(flat_list)

# Filter out single words, keeping only bigrams
#collocations_freq = {k: (v, bigram.phrasegrams[k]) for k, v in collocation_counter.items() if '_' in k}
collocations_freq = {}
for k, v in collocation_counter.items():
    if '_' in k:
        try:
            collocations_freq[k] = (v, bigram.phrasegrams[k])
        except:
            collocations_freq[k] = (v, 0)

In [39]:
bigram_sentences

[['il', 'clima', 'viene', 'controllato', 'con', 'la', 'tecnologia'],
 ['yes',
  'tutto',
  'una',
  'manipolazione',
  'del',
  'clima',
  'adesso',
  'anno',
  'tecnologico',
  'su',
  'tutto',
  'ma',
  'noi',
  'popolo',
  'ni',
  'sappiamo',
  'poco'],
 ['fresco',
  '?',
  'c',
  "'",
  'e',
  'il',
  'rischio',
  'che',
  'non',
  'rimanga',
  'nessun',
  'frutto',
  'tra',
  'grandine',
  ',',
  'neve',
  'e',
  'gelo',
  ',',
  'speriamo_bene',
  '.'],
 ['colpa', 'del', 'riscaldamento_globale'],
 ['questo',
  'io',
  'non',
  'sono',
  'in',
  'grado',
  'di',
  'stabilirlo',
  ',',
  'posso_dire',
  'che',
  'mio',
  'suocero',
  'mi',
  'raccontava',
  'che',
  'il',
  'mese',
  'di',
  'giugno',
  'negli',
  'anni',
  '40/ta',
  'in',
  'molise',
  'gelo',
  'il',
  'grano',
  '.'],
 ['se', 'come', 'no', '!', '!', '!', 'ricaldamento', 'mentale'],
 ['i',
  'politici',
  'stanno',
  'sempre',
  'al',
  'caldo',
  ',',
  'se',
  'slacciassero',
  'la',
  'cravatta',
  ',',
  'fo

In [38]:
collocations_freq_list = sorted(collocations_freq.items(), key=lambda x:-x[1][0])
collocations_freq_list

[('?_?', (3572, 11.3478849713355)),
 ('avanti_tutta', (2172, 60.83887612875759)),
 ('dio_vi_benedica', (2005, 110.17638139197773)),
 ('forza_ragazzi', (1887, 36.97607849366665)),
 ('prodotti_italiani', (1058, 31.65913381352981)),
 ('facebook_.', (854, 11.012728251343432)),
 ('avanti_cosi', (728, 20.003807427814046)),
 ('agricoltori_italiani', (698, 12.10737762907719)),
 ('popolo_italiano', (609, 40.048078832148214)),
 ("po_'", (572, 46.816471121025835)),
 ('buon_lavoro', (489, 55.565515932031765)),
 ('w_gli_agricoltori', (477, 25.99882889919206)),
 ('andate_avanti', (468, 39.00376439791054)),
 ('forza_e_coraggio', (448, 22.352017455404244)),
 ('viva_gli_agricoltori', (446, 19.07117484929326)),
 ('buona_giornata', (420, 256.6120280599159)),
 ('deve_essere', (371, 36.7667867840695)),
 ('altri_paesi', (368, 171.13029124005732)),
 ('tenete_duro', (325, 839.7200494030466)),
 ('fatevi_sentire', (323, 245.20991720415353)),
 ('buona_domenica', (309, 249.32270632102865)),
 ('grazie_mille', (306

In [32]:
sents_w_bigram = bigram[sents]
trigram = Phraser(Phrases(sents_w_bigram, connector_words=stopwords))

In [33]:
trigram_collocations = list()
trigrams_set = set(trigram.phrasegrams.keys())-set(bigram.phrasegrams.keys())
for key in trigrams_set:
    score = trigram.phrasegrams[key]
    trigram_collocations.append((key, score))

In [34]:
# Applying the bigram detector to sentences
trigram_sentences = [trigram[sentence] for sentence in sents_w_bigram]

# Flatten the list of lists
flat_list = [item for sublist in trigram_sentences for item in sublist if item in trigrams_set]

# Counting the frequency of collocations
trigram_collocation_counter = Counter(flat_list)

# Filter out single words, keeping only bigrams
#collocations_freq = {k: (v, bigram.phrasegrams[k]) for k, v in collocation_counter.items() if '_' in k}
trigram_collocations_freq = {}
for k, v in trigram_collocation_counter.items():
    if '_' in k:
        try:
            trigram_collocations_freq[k] = (v, trigram.phrasegrams[k])
        except:
            trigram_collocations_freq[k] = (v, 0)

In [35]:
trigram_collocations_freq_list = sorted(trigram_collocations_freq.items(), key=lambda x:-x[1][0])
trigram_collocations_freq_list

[("'_italia", (530, 10.796685746134159)),
 ('sempre_avanti', (281, 12.37565499140614)),
 ('tutta_italia', (256, 25.110581365280282)),
 ('facebook_._com/story_.', (254, 21.49453791432638)),
 ("l'unione_fa_la_forza", (195, 370.72708206994133)),
 ('w_gli_agricoltori_italiani', (179, 54.90723929479062)),
 ('sempre_italiano', (170, 10.999896148336783)),
 ('cosi_si_fa', (164, 10.703382193103492)),
 ('c.r.a_agricoltori_traditi', (157, 2908.997992515304)),
 ("'_agricoltura", (149, 10.427620757729834)),
 ('mollate_mai', (147, 11.258537353668833)),
 ('dio_ci_benedica', (137, 99.39993992963186)),
 ('deve_fare', (126, 18.102009092411336)),
 ('ora_o_mai', (116, 11.752411366149229)),
 ('devono_fare', (105, 17.78072970058016)),
 ('piu_bella', (105, 11.596863670904705)),
 ('proprio_cosi', (100, 13.950269860545747)),
 ('viva_gli_agricoltori_italiani', (100, 19.666945033497854)),
 ('tutta_europa', (97, 26.666539044787772)),
 ('vogliono_fare', (93, 10.616591206641731)),
 ('youtube_._com/watch_?', (93, 63

# n grammi

In [54]:
def def_value(): 
    return 0

all_2grams = list()
freq_2grams = defaultdict(def_value)
for text in comments_truncated["content"]:
    temp = list(nltk.ngrams(nltk.word_tokenize(transform_text(text), language='italian'), 2)) 
    for ngram in temp:
        for token in ngram:
            if token not in stopwords:
                all_2grams.append("_".join(list(ngram)))
                freq_2grams["_".join(list(ngram))] = freq_2grams["_".join(list(ngram))] + 1
                break

In [55]:
sorted(freq_2grams.items(), key=lambda x:-x[1])

[('gli_agricoltori', 4590),
 ('non_mollate', 3592),
 ('dio_vi', 2609),
 ('a_roma', 2282),
 ('vi_benedica', 2221),
 ('che_dio', 2218),
 ('avanti_tutta', 2182),
 ('il_popolo', 1963),
 ('in_italia', 1936),
 ('forza_ragazzi', 1887),
 ('tutte_le', 1425),
 ('la_terra', 1305),
 ('gli_italiani', 1198),
 ('prodotti_italiani', 1089),
 ('i_prodotti', 1041),
 ('agricoltori_italiani', 1036),
 ('agricoltori_,', 1028),
 ('a_casa', 1004),
 ('sempre_con', 1000),
 ('cio_che', 946),
 ('e_poi', 920),
 ('non_solo', 890),
 ('facebook_.', 860),
 ('il_governo', 857),
 ('un_po', 856),
 (',_perche', 855),
 ('non_mollare', 846),
 ('avanti_cosi', 837),
 ('perche_non', 829),
 ('di_piu', 822),
 ('a_fare', 778),
 ('si_puo', 778),
 ('degli_agricoltori', 776),
 ('forza_e', 775),
 ('i_politici', 768),
 ('si_fa', 761),
 ('gli_altri', 752),
 ('..._e', 749),
 ('la_gente', 741),
 ('agricoltori_e', 711),
 ('tutti_uniti', 706),
 ('grazie_a', 698),
 ('in_piazza', 686),
 ('e_solo', 684),
 ('italiani_,', 680),
 ('il_problema', 

In [41]:
list(nltk.ngrams(nltk.word_tokenize('I won, and thus, you lose.'),2))

[('I', 'won'),
 ('won', ','),
 (',', 'and'),
 ('and', 'thus'),
 ('thus', ','),
 (',', 'you'),
 ('you', 'lose'),
 ('lose', '.')]

In [57]:
def def_value(): 
    return 0

all_3grams = list()
freq_3grams = defaultdict(def_value)
for text in comments_truncated["content"]:
    temp = list(nltk.ngrams(nltk.word_tokenize(transform_text(text), language='italian'), 3)) 
    for ngram in temp:
        for token in ngram:
            if token not in stopwords:
                all_3grams.append("_".join(list(ngram)))
                freq_3grams["_".join(list(ngram))] = freq_3grams["_".join(list(ngram))] + 1
                break

In [58]:
sorted(freq_3grams.items(), key=lambda x:-x[1])

[('dio_vi_benedica', 2005),
 ('che_dio_vi', 1583),
 ('sempre_con_voi', 760),
 ('gli_agricoltori_italiani', 665),
 ('tutti_gli_agricoltori', 577),
 ("un_po_'", 564),
 ('con_gli_agricoltori', 538),
 ('tutti_a_roma', 536),
 ('i_nostri_prodotti', 509),
 ('w_gli_agricoltori', 477),
 ('forza_e_coraggio', 448),
 ('i_nostri_agricoltori', 448),
 ('viva_gli_agricoltori', 446),
 ("l_'_italia", 431),
 ('non_mollate_!', 426),
 ('gli_agricoltori_,', 390),
 ('il_popolo_e', 387),
 ('avanti_tutta_!', 373),
 ('solo_prodotti_italiani', 362),
 ('il_popolo_italiano', 360),
 ('la_terra_e', 350),
 ('forza_!_!', 323),
 ('quello_che_fate', 317),
 ('non_si_puo', 311),
 ('la_nostra_terra', 308),
 ('non_mollate_,', 304),
 ('forza_siamo_con', 302),
 ('fa_la_forza', 299),
 ('vi_benedica_e', 294),
 ('forza_non_mollate', 294),
 (',_non_mollate', 290),
 ('la_nostra_agricoltura', 288),
 ('tutti_gli_italiani', 286),
 ('frutta_e_verdura', 284),
 ('grazie_a_tutti', 280),
 ('e_che_dio', 279),
 ('gli_agricoltori_e', 275),
 

In [60]:
def def_value(): 
    return 0

all_4grams = list()
freq_4grams = defaultdict(def_value)
for text in comments_truncated["content"]:
    temp = list(nltk.ngrams(nltk.word_tokenize(transform_text(text), language='italian'), 4)) 
    for ngram in temp:
        for token in ngram:
            if token not in stopwords:
                all_4grams.append("_".join(list(ngram)))
                freq_4grams["_".join(list(ngram))] = freq_4grams["_".join(list(ngram))] + 1
                break

In [62]:
sorted(freq_4grams.items(), key=lambda x:-x[1])

[('che_dio_vi_benedica', 1206),
 ('a_tutti_gli_agricoltori', 286),
 ('forza_siamo_con_voi', 278),
 ('dio_vi_benedica_e', 258),
 ('facebook_._com/story_.', 254),
 ('._com/story_._php', 253),
 ('forza_!_!_!', 249),
 ('com/story_._php_?', 236),
 ('non_mollate_!_!', 233),
 ("un_po_'_di", 228),
 ('avanti_tutta_!_!', 227),
 ('dio_vi_benedica_!', 218),
 ('bravi_!_!_!', 203),
 ('il_popolo_e_con', 197),
 ('grandi_!_!_!', 197),
 ("l'unione_fa_la_forza", 195),
 ('popolo_e_con_voi', 183),
 ('vi_benedica_e_vi', 182),
 ('w_gli_agricoltori_italiani', 179),
 ('e_che_dio_vi', 178),
 ('tutta_!_!_!', 178),
 ('dio_vi_benedica_sempre', 174),
 ('mollate_!_!_!', 174),
 ('per_quello_che_fate', 170),
 ('grazie_per_quello_che', 156),
 ('da_nord_a_sud', 152),
 ('!_!_!_forza', 150),
 ('in_bocca_al_lupo', 147),
 ('ragazzi_siamo_con_voi', 142),
 ('non_mollate_siamo_con', 140),
 ('quello_che_state_facendo', 139),
 ('mollate_siamo_con_voi', 139),
 ('agricoltori_!_!_!', 138),
 ("l'italia_e_con_voi", 135),
 ('una_richi

In [61]:
def def_value(): 
    return 0

all_5grams = list()
freq_5grams = defaultdict(def_value)
for text in comments_truncated["content"]:
    temp = list(nltk.ngrams(nltk.word_tokenize(transform_text(text), language='italian'), 5)) 
    for ngram in temp:
        for token in ngram:
            if token not in stopwords:
                all_5grams.append("_".join(list(ngram)))
                freq_5grams["_".join(list(ngram))] = freq_5grams["_".join(list(ngram))] + 1
                break

In [63]:
sorted(freq_5grams.items(), key=lambda x:-x[1])

[('facebook_._com/story_._php', 253),
 ('._com/story_._php_?', 236),
 ('il_popolo_e_con_voi', 177),
 ('non_mollate_!_!_!', 172),
 ('avanti_tutta_!_!_!', 169),
 ('dio_vi_benedica_e_vi', 160),
 ('e_che_dio_vi_benedica', 141),
 ('che_dio_vi_benedica_!', 140),
 ('non_mollate_siamo_con_voi', 132),
 ('che_dio_vi_benedica_e', 129),
 ('forza_!_!_!_!', 128),
 ('grazie_per_quello_che_fate', 116),
 ('io_sto_con_gli_agricoltori', 112),
 ('il_futuro_dei_nostri_figli', 108),
 ('bravi_!_!_!_!', 104),
 ('che_dio_vi_benedica_sempre', 98),
 ('forza_siamo_tutti_con_voi', 98),
 ('forza_ragazzi_siamo_con_voi', 96),
 ('vi_benedica_e_vi_protegga', 95),
 ('grazie_grazie_grazie_grazie_grazie', 93),
 ('grandi_!_!_!_!', 92),
 ("non_c_'_e_piu", 89),
 ('mollate_!_!_!_!', 87),
 (',_che_dio_vi_benedica', 80),
 ('tutta_!_!_!_!', 78),
 ('grazie_a_tutti_gli_agricoltori', 69),
 ('forza_ragazzi_!_!_!', 64),
 ('w_gli_agricoltori_italiani_!', 63),
 ('che_dio_vi_benedica_,', 63),
 ('gli_agricoltori_!_!_!', 62),
 ('per_quell

# Entità

In [11]:
import requests # For REST calls
import json # for modelling objects in the JSON format

In [12]:
# This line opens the file from the file system, the file is in the same folder of the notebook and it is opened in "read-only mode"
with open("config.json", 'r') as json_file:
    config = json.load(json_file) # load the json object inside the config file
    KEY = config['d4science_KEY'] # this is the key we will be using for REST calls

In [13]:
TAGME_ENDPOINT = "https://tagme.d4science.org/tagme/tag"
LANG = "it" # Also works in italian and german

In [14]:
def query_tagme(text, long_text=False):
    payload = {"text": text, "gcube-token": KEY, "lang": LANG}
    if long_text:
        # long_text is by defaul false, but if specified by the user, we set the window size at 5
        payload["long_text"] = 5
    r = requests.post(TAGME_ENDPOINT, payload)
    if r.status_code != 200:
        raise Exception("Error on text: {}\n{}".format(text, r.text))
    return r.json()

In [15]:
# Try changing the min_rho parameter and see how it impacts the returned entities
def get_tagme_entities(tagme_response, min_rho=0.3, min_link_probability=0.1):
    ann = tagme_response["annotations"]
    ann = [a for a in ann if a["rho"] > min_rho and a["link_probability"] > min_link_probability] # filter all the annotations with a rho score lower than the threshold
    return [a["title"] for a in ann if "title" in a] # return just the page titles

In [20]:
def def_value(): 
    return 0

count = 0
all_entities = []
entities_freq = defaultdict(def_value)
for text in comments_truncated.iloc[:80000]["content"]:
    try:
        resp = query_tagme(transform_text(text), long_text=True) 
    except:
        continue
    count = count + 1
    print(count)
    for entity in get_tagme_entities(resp):
        all_entities.append(entity)
        entities_freq[entity] = entities_freq[entity] + 1

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247


In [ ]:
text = "prova"
resp = query_tagme(text, long_text=True)
print(resp)